<img src="https://unidata.ucar.edu/images/logos/badges/badge_unidata_100.jpg" alt="Unidata Logo" style="float: right; height: 98px;">

# Siphon THREDDS Jupyter Notebook Viewer

## Dataset: EREEFS_AIMS-CSIRO_gbr1_2.0_hydro_daily-daily-2023-02-17.nc
___

### Introduction
This Jupyter Notebook was written to help you understand how to access and explore eReefs' data.
The code is split into small code blocks called cells.
You will find comment cells between code cells which describe what the code is doing.

All the eReefs' datasets are hosted in the cloud, using AWS S3 services.
Initialising a connection to the data and extracting the data sometime take several minutes.
Please, be patient.

### How to use this Notebook
1) Select the the code cell you want to execute by click in its margin.
2) Press `Shift + Enter` to execute it.

**NOTE**: The code is designed to be executed sequentially, from the first cell to the last one.
You can modify the code, but you will need to re-execute the modified cell and subsequent cells.
Your modifications are not permanent. Jupyter Notebooks are only intended to be used to explore the Python code.
___

### Dependencies
This Jupyter Notebook uses several libraries to access the data remotely and plot it.

* *Siphon*: `pip install siphon`
* *matplotlib*: `pip install matplotlib` or `conda install -c conda-forge matplotlib`
* *ipywidgets*: `pip install ipywidgets` or `conda install -c conda-forge ipywidgets`
* enable *ipywidgets*:
    * using Juputer Notebooks: `jupyter nbextension enable --py widgetsnbextension`
    * using JupyterLab:
        * nodejs: `conda install nodejs`
        * `jupyter labextension install @jupyter-widgets/jupyterlab-manager`
* *numpy*: `pip install numpy` or `conda install numpy`
___

In [ ]:
# Load dependencies
from siphon.catalog import TDSCatalog
import matplotlib.pyplot as plt
import numpy as np
import ipywidgets as widgets
from netCDF4 import num2date

In [ ]:
# Initialise variables specific to this dataset
catUrl = "https://thredds.ereefs.aims.gov.au/thredds/catalog/ereefs/gbr1_2.0/daily-daily/catalog.xml"
datasetName = "EREEFS_AIMS-CSIRO_gbr1_2.0_hydro_daily-daily-2023-02-17.nc"

### Access a dataset
With the TDS catalog url, we can use [Siphon](https://unidata.github.io/siphon/latest/) to get the dataset.

In [ ]:
catalog = TDSCatalog(catUrl)

In [ ]:
ds = catalog.datasets[datasetName]
ds.name

Each dataset support a set of access protocols.

Execute the next cell to list the protocols available for this dataset.

In [ ]:
list(ds.access_urls)

Siphon's `remote-access` returns a `Dataset` object, which opens the remote dataset and provides access to its metadata.

By default, the `remote-access` method access the data using the `CdmRemote` protocol.
It's also possible to request the data with the `OpenDAP` protocol using the `netCDF4` python library.

**NOTE**: This operation may take several minutes. Please, be patient.

In [ ]:
dataset = ds.remote_access()

### Display a variable
Now that we have access to the dataset, we need to select a variable to work with.
We can use the [ipywidgets](https://ipywidgets.readthedocs.io/) library to generate a list of radio button for all the available variables.

1) Create a widget to select from a list of all variables in this dataset.

In [ ]:
var_name = widgets.RadioButtons(
    options=list(dataset.variables),
    description='Variable:')

2) Display the widget and select the variable you wish to view.

In [ ]:
display(var_name)

### Find dimension variables
Each variable have a set of dimensions. For example: `[time, depth, longitude, latitude]`.
We extract the list of dimensions from the selected variable using `var.dimensions`
then we look through all to variables to find which one is used to represent each dimension.

In [ ]:
# Find time, depth, longitude and latitude dimension variables
var = dataset.variables[var_name.value]
dimensions = var.dimensions

time_dim_var = None
depth_dim_var = None
longitude_dim_var = None
latitude_dim_var = None

# Only attempt to find dimension variables if the selected variable is not itself a dimension variable.
if 'coordinate_type' not in var.ncattrs():
    for dim_var in dataset.variables.values():
        # Only Dimension variables have the attribute 'coordinate_type'
        if 'coordinate_type' in dim_var.ncattrs():
            # The following test check if the dimension variable we found (dim_var) is used by our selected variable (var).
            # This is done by checking if the dimension of dim_var is in the list of dimension of the selected variable.
            # NOTE: Dimension variables usually only have 1 dimension.
            if dim_var.dimensions[0] in dimensions:
                if dim_var.coordinate_type == 'time':
                    time_dim_var = dim_var
                elif dim_var.coordinate_type == 'Z':
                    depth_dim_var = dim_var
                elif dim_var.coordinate_type == 'longitude':
                    longitude_dim_var = dim_var
                elif dim_var.coordinate_type == 'latitude':
                    latitude_dim_var = dim_var

print("Dimensions: " + str(list(dimensions)))
print("Time dimension variable: " + (time_dim_var.name if time_dim_var is not None else "N/A"))
print("Depth dimension variable: " + (depth_dim_var.name if depth_dim_var is not None else "N/A"))
print("Longitude dimension variable: " + (longitude_dim_var.name if longitude_dim_var is not None else "N/A"))
print("Latitude dimension variable: " + (latitude_dim_var.name if latitude_dim_var is not None else "N/A"))

3) Select the date and time you wish to view.

**NOTE**: The widget will only be displayed if the selected variable have a time dimension.

In [ ]:
if time_dim_var is not None:
    time_values = time_dim_var[:].squeeze()
    time_cfdates = num2date(time_values, time_dim_var.units)
    # time_labels = [i.isoformat() for i in time_cfdates]
    time_options = np.vstack((time_cfdates, time_values)).T.tolist()
    time = widgets.RadioButtons(
        options=time_options,
        description='Time:')
    display(time)

In [ ]:
time_value_index = None
if time_dim_var is not None:
    time_value_index = time_values.tolist().index(time.value)
    display("Date/time value: " + str(time.value) + ", array index: " + str(time_value_index))

4) Select the depth you wish to view.

**NOTE**: The widget will only be displayed if the selected variable have a depth dimension.

In [ ]:
if depth_dim_var is not None:
    depth_values = depth_dim_var[:].squeeze()
    depth = widgets.RadioButtons(
        options=depth_values,
        description='Depth:')
    display(depth)

In [ ]:
depth_value_index = None
if depth_dim_var is not None:
    depth_value_index = depth_values.tolist().index(depth.value)
    display("Depth: " + str(depth.value) + ", array index: " + str(depth_value_index))

5) Extract relevant data from the dataset

**NOTE**: This operation may take several minutes. Please, be patient.

In [ ]:
var_subset = var
if time_dim_var is not None and depth_dim_var is not None:
    var_subset = var[time_value_index, depth_value_index, :, :]
elif time_dim_var is not None:
    var_subset = var[time_value_index, :, :]
elif depth_dim_var is not None:
    var_subset = var[depth_dim_var, :, :]

6) Display information about the chosen variable, depth and time

In [ ]:
shape = np.array(var_subset.shape)
print("Name: " + var.name)
print("Dimensions: " + str(list(dimensions)))
print("Shape of the data selected: " + str(shape))
import operator
from functools import reduce
nelems = reduce(operator.mul, shape, 1)
print("Number of elements: " + str(nelems))
print("Datatype: " + str(var.dtype))

7) Run a few test to make sure the variable can be plotted.

In [ ]:
# Inspect NetCDF file
is_numeric = var.dtype == np.uint8 or np.can_cast(var.dtype, float, "same_kind")
ndims = len([s for s in shape if s > 1])
max_dims = 2

In [ ]:
# only attempt to plot numeric types
if (not(is_numeric)):
    print("Not a numeric type - cannot plot variable: ", var.name)

In [ ]:
# assure plotable number of dimensions
if (ndims > max_dims):
    print("Too many dimensions - reducing last " + str(ndims-max_dims) + " dimensions.")
    shape[np.argwhere(shape>1).flatten().tolist()[max_dims:]] = 1
    print("New shape: " + str(shape))
    ndims = max_dims

8) Attempt to plot the variable using [matplotlib.pyplot](https://matplotlib.org/stable/api/pyplot_summary.html).

In [ ]:
# plot the variable
%matplotlib inline
# for zero-dimensional data, print value
if (ndims == 0):
    print(var.name, ": ", var_subset)
# for one-dimensional data, make a line plot
elif (ndims == 1):
    plt.plot(np.squeeze(np.array([range(len(np.squeeze(var_subset[:])))])), np.squeeze(var_subset[:]), 'bo', markersize=5)
    plt.title(var.name)
    plt.show()
# for two-dimensional data, make an image
elif (ndims == 2):
    # Calculate longitude (x) min/max values
    longitude_values = longitude_dim_var[:].squeeze()
    longitude_min = longitude_values.min()
    longitude_max = longitude_values.max()

    # Calculate latitude (y) min/max values
    latitude_values = latitude_dim_var[:].squeeze()
    latitude_min = latitude_values.min()
    latitude_max = latitude_values.max()

    plt.imshow(np.squeeze(var_subset[:]), origin="lower", extent=[longitude_min, longitude_max, latitude_min, latitude_max])
    plt.title(var.name)
    plt.show()

**NOTE**: Data are only transferred over the network when the variable is sliced, and only data corresponding to the slice are downloaded.

---

9) To plot a different variable, select it in the widget and rerun the subsequent cells.

### More with Siphon
To see what else you can do, view the [Siphon API](https://unidata.github.io/siphon/latest/api/index.html).

In [ ]:
### Your code here ###